In [16]:
# Работа с табличными данными

import pandas as pd
import numpy as np


# Визуализация

import plotly.express as px
import plotly.io as pio
pio.templates.default = 'plotly_dark'
pio.renderers.default = 'notebook'
from motorica.emg8.utils import fig_montage # кастомная функция визуализации


# Пайплайн

# константы
from motorica.emg8.constants import *
# чтение данных и разметка по фактическим жестам
from motorica.emg8.pipeline import read_emg8
from motorica.emg8.markers import BasePeakMarker, TransMarker
# создание экземпляра пайплайна
from motorica.emg8.pipeline import create_grad_logreg_pipeline


# Метрики
from sklearn.metrics import classification_report, f1_score


# Для вывода докстрингов с форматированием markdown
from IPython.display import Markdown as md

# Работа с файлами
import os

# Для оценки скорости инференса
from time import time

# Сериализация модели (пайплайна)
import pickle

## Подгрузка и разметка данных

Список имеющихся файлов с данными:

In [17]:
# Папка с файлами данных
# DATA_DIR = 'data/plt_mb/all'
DATA_DIR = 'data/plt_n'

montages = sorted(filter(lambda f: f.endswith('.emg8'), os.listdir(DATA_DIR)))
montages

['2024-11-11_18-46-48.emg8',
 '2024-11-11_19-42-26.emg8',
 '2024-11-12_11-17-31.emg8',
 '2024-11-12_11-35-21.emg8',
 '2024-11-12_13-26-05.emg8',
 '2024-11-12_13-39-57.emg8']

In [18]:
montage = montages[2]
gestures_raw = pd.read_csv(os.path.join(DATA_DIR, montage), sep=' ')
fig_montage(
    gestures_raw[OMG_CH], y_cmd=gestures_raw['id'], 
    title=f"<i>{montage}</i> – исходные данные"
).show()

In [19]:
n_holdout_groups = 1 # отложенная выборка - последний цикл протокола

marker = BasePeakMarker()

X_train, X_test, y_train, y_test, gestures, cv_groups = read_emg8(
    montage, dir=DATA_DIR,
    n_holdout_groups=n_holdout_groups,
    marker=marker
)

last_train_idx = gestures[GROUP_COL].drop_duplicates().index[-n_holdout_groups] - 1

print('X_train shape:', X_train.shape)
print('y_train shape:', y_train.shape)
print('X_test shape:', X_test.shape)
print('y_test shape:', y_test.shape)

state_id = gestures[['id', 'state']].drop_duplicates()
GESTURES = state_id['state'] + ' ' + state_id['id'].astype(str)
display(GESTURES)

display

fig_montage(
    gestures[OMG_CH], 
    y_cmd=gestures[CMD_COL], 
    y_act=gestures[TARGET],
    protocol_cycle=gestures[GROUP_COL],
    # grad2=marker.peaks_grad2 / 2,
    # grad2_neg=marker.peaks_grad2_neg / 2,
    # std1=marker.peaks_std1 / 2,
    # std1_neg=marker.peaks_std1_neg / 2,
    title=f"<i>{montage}</i> – разметка по фактическим границам жестов"
).show()

X_train shape: (4008, 16)
y_train shape: (4008,)
X_test shape: (1054, 16)
y_test shape: (1054,)


126          Neutral 0
225     ThumbFingers 1
363            Close 2
500             Open 3
638            Pinch 4
775       Indication 5
913       Wrist_Flex 6
1050    Wrist_Extend 7
dtype: object

In [20]:
# n_holdout_groups = 1

trans_marker = TransMarker(use_peaks='std', bounds_shift=0)
X_train_trans, X_test_trans, y_train_trans, y_test_trans, gestures_trans, cv_groups_trans = read_emg8(
    montage, dir=DATA_DIR,
    n_holdout_groups=1,
    marker=trans_marker
)

last_train_idx_trans = gestures[GROUP_COL].drop_duplicates().index[-n_holdout_groups] - 1

print('X_train shape:', X_train_trans.shape)
print('y_train shape:', y_train_trans.shape)
print('X_test shape:', X_test_trans.shape)
print('y_test shape:', y_test_trans.shape)

fig_montage(
    gestures_trans[OMG_CH], 
    y_cmd_trans=gestures_trans[CMD_COL], 
    y_act=gestures_trans[TARGET],
    protocol_cycle=gestures_trans[GROUP_COL],
    # peaks=trans_marker.peaks_std1 / 2,
    # peaks_neg=-trans_marker.peaks_std1_neg / 2,
    # grad2=marker.peaks_grad2 / 2,
    # grad2_neg=marker.peaks_grad2_neg / 2,
    # std1=marker.peaks_std1 / 2,
    # std1_neg=marker.peaks_std1_neg / 2,
    title=f"<i>{montage}</i> – разметка жестов с переходами"
).show()

X_train shape: (4090, 16)
y_train shape: (4090,)
X_test shape: (972, 16)
y_test shape: (972,)


## Пайплайн

In [21]:
model = create_grad_logreg_pipeline(exec_optimize=False, exec_fit=False, X=X_train, y=y_train)
model

Pipeline(steps=[('fix_1dim_sample', FixOneDimSample()),
                ('noise_reduct', NoiseReduction()),
                ('gradients', Gradients(oper='add')),
                ('scaler', MinMaxScaler()), ('model', TransWrapper())])

In [22]:
# # сохранение пайплайна (сериализация)
# with open('pipeline_logreg.pkl', 'wb') as f:
#     pickle.dump(model, f)

# # восстановление пайплайна из файла
# with open('pipeline_logreg.pkl', 'rb') as f:
#     model = pickle.load(f)

## Симуляция инференса в реальном времени на отложенной выборке

In [23]:
# 1. Без предсказания переходов

model.fit(X_train, y_train)

y_test_pred = np.empty(0)
comp_durations = np.empty(0)

for i in range(X_test.shape[0]):
    start_time = time()
    y_test_pred = np.append(y_test_pred, model.predict(X_test[i]))
    comp_duration = time() - start_time
    comp_durations = np.append(comp_durations, comp_duration)

print(f"Максимальное время: {np.round(comp_durations.max() * 1000, 2)} мс")
print(f"Среднее время: {np.round(comp_durations.mean() * 1000, 2)} мс")

print(classification_report(y_test, y_test_pred, target_names=GESTURES, zero_division=0))

fig = fig_montage(
    pd.DataFrame(X_test), 
    y_cmd=gestures.loc[last_train_idx + 1:, CMD_COL].reset_index(drop=True), 
    y_true=y_test, y_pred=y_test_pred,
    title=f"{montage}<br>Результаты предсказаний в инференсе <b>без использования переходов</b>"
)
fig.show()


# 2. С использованием доополнительных классов переходов

model.fit(X_train_trans, y_train_trans)

y_test_trans[y_test_trans < 0] = 0
y_test_trans %= 10

y_test_pred = np.empty(0)
comp_durations = np.empty(0)

for i in range(X_test_trans.shape[0]):
    start_time = time()
    y_test_pred = np.append(y_test_pred, model.predict(X_test_trans[i]))
    comp_duration = time() - start_time
    comp_durations = np.append(comp_durations, comp_duration)

print(f"Максимальное время: {np.round(comp_durations.max() * 1000, 2)} мс")
print(f"Среднее время: {np.round(comp_durations.mean() * 1000, 2)} мс")

print(classification_report(y_test_trans, y_test_pred, target_names=GESTURES, zero_division=0))

fig = fig_montage(
    pd.DataFrame(X_test_trans), 
    y_cmd=gestures.loc[last_train_idx + 1:, CMD_COL].reset_index(drop=True), 
    y_true=y_test_trans, y_pred=y_test_pred,
    title=f"{montage}<br>Результаты предсказаний в инференсе <b>с использованием переходов</b>"
)
fig.show()

Максимальное время: 2.33 мс
Среднее время: 0.34 мс
                precision    recall  f1-score   support

     Neutral 0       0.88      0.98      0.92       729
ThumbFingers 1       1.00      0.52      0.69        65
       Close 2       1.00      0.54      0.70        61
        Open 3       1.00      0.40      0.57        35
       Pinch 4       1.00      0.77      0.87        44
  Indication 5       1.00      0.22      0.36        46
  Wrist_Flex 6       0.35      0.85      0.50        33
Wrist_Extend 7       0.85      0.80      0.82        41

      accuracy                           0.85      1054
     macro avg       0.88      0.64      0.68      1054
  weighted avg       0.89      0.85      0.84      1054



Максимальное время: 22.79 мс
Среднее время: 0.43 мс
                precision    recall  f1-score   support

     Neutral 0       0.83      0.84      0.84       683
ThumbFingers 1       0.00      0.00      0.00        27
       Close 2       1.00      0.49      0.66        61
        Open 3       0.93      0.72      0.81        36
       Pinch 4       1.00      0.82      0.90        44
  Indication 5       0.95      0.82      0.88        45
  Wrist_Flex 6       0.69      0.85      0.76        34
Wrist_Extend 7       0.00      0.00      0.00        42

      accuracy                           0.76       972
     macro avg       0.67      0.57      0.61       972
  weighted avg       0.79      0.76      0.77       972



## Сравнение результатов предстказаний с применением классов-переходов и без них

In [24]:
results = []

for montage in montages:
    scores = []
    for marker in [
        BasePeakMarker(),
        TransMarker(use_peaks='std', bounds_shift=0)
    ]:
        X_train, X_test, y_train, y_test, *_ = read_emg8(montage, dir=DATA_DIR, marker=marker, n_holdout_groups=1)
        y_test[y_test < 0] = 0
        y_test %= 10
        model = create_grad_logreg_pipeline(X_train, y_train, exec_fit=True)
        y_pred = model.predict(X_test)
        score = f1_score(y_test, y_pred, average='macro')

        scores.append(np.round(score, 2))
    results.append(scores)

In [25]:
results = pd.DataFrame(results, columns=['no transitions', 'use transitions'], index=montages)
display(results)
px.bar(
    results, y=['no transitions', 'use transitions'], 
    barmode='group', 
    width=1000, height=600,
    text_auto=True,
    title=DATA_DIR
)

no transitions  use transitions
2024-11-11_18-46-48.emg8            0.83             0.72
2024-11-11_19-42-26.emg8            0.76             0.57
2024-11-12_11-17-31.emg8            0.68             0.61
2024-11-12_11-35-21.emg8            0.83             0.87
2024-11-12_13-26-05.emg8            0.89             0.90
2024-11-12_13-39-57.emg8            0.90             0.90

In [26]:
marker = TransMarker(use_peaks='std', bounds_shift=0)
nogo_data = np.empty((0, N_OMG_CH))

for montage in montages:

    X, _, y, _, gestures, _ = read_emg8(montage, dir=DATA_DIR, marker=marker)
    # print(gestures['act_label'].value_counts())
    
    mask = gestures['act_label'] == marker.states[FLEX_STATE]
    gestures_nogo = gestures[mask]
    omg_means = gestures_nogo.groupby(SYNC_COL)[OMG_CH].mean()
    # omg_means = pd.DataFrame(gestures_nogo[OMG_CH].median()).T
    nogo_data = np.concatenate([nogo_data, omg_means], axis=0)
    

In [27]:
px.imshow(nogo_data.T, width=1500, height=500).update_coloraxes(showscale=False)